In [122]:
import pandas as pd
import numpy as np# library to handle data in a vectorized manner
import requests
!pip install lxml
!pip install geocoder
import urllib.request
 

In [0]:
#scrap toronto neighbourhoods from wikipedia

In [0]:
website_url = requests.get("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M").text




In [125]:
from bs4 import BeautifulSoup
soup = BeautifulSoup(website_url,"lxml")
print(soup.prettify())


<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of postal codes of Canada: M - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_postal_codes_of_Canada:_M","wgTitle":"List of postal codes of Canada: M","wgCurRevisionId":920980179,"wgRevisionId":920980179,"wgArticleId":539066,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Communications in Ontario","Postal codes in Canada","Toronto","Ontario-related lists"],"wgBreakFrames":!1,"wgPageContentLanguage":"en","wgPageContentModel":"wikitext","wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgMonthNames

In [126]:
from tabulate import tabulate
table = soup.find_all('table')[0] 
df = pd.read_html(str(table))
print( tabulate(df[0], headers='keys', tablefmt='psql') )

+-----+------------+------------------+---------------------------------------------------+
|     | Postcode   | Borough          | Neighbourhood                                     |
|-----+------------+------------------+---------------------------------------------------|
|   0 | M1A        | Not assigned     | Not assigned                                      |
|   1 | M2A        | Not assigned     | Not assigned                                      |
|   2 | M3A        | North York       | Parkwoods                                         |
|   3 | M4A        | North York       | Victoria Village                                  |
|   4 | M5A        | Downtown Toronto | Harbourfront                                      |
|   5 | M5A        | Downtown Toronto | Regent Park                                       |
|   6 | M6A        | North York       | Lawrence Heights                                  |
|   7 | M6A        | North York       | Lawrence Manor                          

In [127]:
df1 = pd.DataFrame.from_records(df[0])
df1.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

In [60]:
df1.drop(df1.loc[df1['Borough']=="Not assigned"].index, inplace=True)
df1.head()

Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M5A  Downtown Toronto       Regent Park
6      M6A        North York  Lawrence Heights

In [128]:
toronto_df=df1.groupby(['Postcode','Borough'],sort=False,as_index=False).agg(lambda x: ','.join(x))
toronto_df.head()

Postcode           Borough             Neighbourhood
0      M1A      Not assigned              Not assigned
1      M2A      Not assigned              Not assigned
2      M3A        North York                 Parkwoods
3      M4A        North York          Victoria Village
4      M5A  Downtown Toronto  Harbourfront,Regent Park

In [129]:
toronto_df.loc[toronto_df['Neighbourhood'] == "Not assigned", 'Neighbourhood'] = toronto_df['Borough']
toronto_df.head()

Postcode           Borough             Neighbourhood
0      M1A      Not assigned              Not assigned
1      M2A      Not assigned              Not assigned
2      M3A        North York                 Parkwoods
3      M4A        North York          Victoria Village
4      M5A  Downtown Toronto  Harbourfront,Regent Park

In [0]:
#Get latitudes and longitudes of neighbourhoods

In [0]:
toronto_postalcodes="https://cocl.us/Geospatial_data"

In [0]:
pc_df=pd.read_csv("https://cocl.us/Geospatial_data")

In [133]:

pc_df.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [0]:
pc_df.columns=['Postcode','Latitude','Longitude']

In [135]:
pc_df.head()

Postcode   Latitude  Longitude
0      M1B  43.806686 -79.194353
1      M1C  43.784535 -79.160497
2      M1E  43.763573 -79.188711
3      M1G  43.770992 -79.216917
4      M1H  43.773136 -79.239476

In [0]:
toronto_df1=pd.merge(toronto_df,pc_df,on='Postcode')

In [137]:
toronto_df1.head()

Postcode           Borough  ...   Latitude  Longitude
0      M3A        North York  ...  43.753259 -79.329656
1      M4A        North York  ...  43.725882 -79.315572
2      M5A  Downtown Toronto  ...  43.654260 -79.360636
3      M6A        North York  ...  43.718518 -79.464763
4      M7A      Queen's Park  ...  43.662301 -79.389494

[5 rows x 5 columns]

In [0]:
import matplotlib.cm as cm
import matplotlib.colors as colors # Matplotlib and associated plotting modules
from sklearn.cluster import KMeans# import k-means from clustering stage
import folium # map rendering library
from geopy.geocoders import Nominatim# convert an address into latitude and longitude values


In [139]:
toronto_data = toronto_df1[toronto_df1['Borough'].str.contains('Toronto')].reset_index(drop=True)
toronto_data


Postcode           Borough  ...   Latitude  Longitude
0       M5A  Downtown Toronto  ...  43.654260 -79.360636
1       M5B  Downtown Toronto  ...  43.657162 -79.378937
2       M5C  Downtown Toronto  ...  43.651494 -79.375418
3       M4E      East Toronto  ...  43.676357 -79.293031
4       M5E  Downtown Toronto  ...  43.644771 -79.373306
5       M5G  Downtown Toronto  ...  43.657952 -79.387383
6       M6G  Downtown Toronto  ...  43.669542 -79.422564
7       M5H  Downtown Toronto  ...  43.650571 -79.384568
8       M6H      West Toronto  ...  43.669005 -79.442259
9       M5J  Downtown Toronto  ...  43.640816 -79.381752
10      M6J      West Toronto  ...  43.647927 -79.419750
11      M4K      East Toronto  ...  43.679557 -79.352188
12      M5K  Downtown Toronto  ...  43.647177 -79.381576
13      M6K      West Toronto  ...  43.636847 -79.428191
14      M4L      East Toronto  ...  43.668999 -79.315572
15      M5L  Downtown Toronto  ...  43.648198 -79.379817
16      M4M      East Toronto  ...  43.659526 -79.340923
17      M4N   Central Toronto  ...  43.728020 -79.388790
18      M5N   Central Toronto  ...  43.711695 -79.416936
19      M4P   Central Toronto  ...  43.712751 -79.390197
20      M5P   Central Toronto  ...  43.696948 -79.411307
21      M6P      West Toronto  ...  43.661608 -79.464763
22      M4R   Central Toronto  ...  43.715383 -79.405678
23      M5R   Central Toronto  ...  43.672710 -79.405678
24      M6R      West Toronto  ...  43.648960 -79.456325
25      M4S   Central Toronto  ...  43.704324 -79.388790
26      M5S  Downtown Toronto  ...  43.662696 -79.400049
27      M6S      West Toronto  ...  43.651571 -79.484450
28      M4T   Central Toronto  ...  43.689574 -79.383160
29      M5T  Downtown Toronto  ...  43.653206 -79.400049
30      M4V   Central Toronto  ...  43.686412 -79.400049
31      M5V  Downtown Toronto  ...  43.628947 -79.394420
32      M4W  Downtown Toronto  ...  43.679563 -79.377529
33      M5W  Downtown Toronto  ...  43.646435 -79.374846
34      M4X  Downtown Toronto  ...  43.667967 -79.367675
35      M5X  Downtown Toronto  ...  43.648429 -79.382280
36      M4Y  Downtown Toronto  ...  43.665860 -79.383160
37      M7Y      East Toronto  ...  43.662744 -79.321558

[38 rows x 5 columns]

In [140]:
address = 'Toronto,Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


In [141]:
# create map of Toronto Borough using latitude and longitude values
map_Torontobh = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(toronto_data['Latitude'], toronto_data['Longitude'], toronto_data['Neighbourhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Torontobh)  
    
map_Torontobh

In [142]:
CLIENT_ID = '3RTK0YFFDQHCXD5RAYGWJXMMT1OJ05QBOJVRNU4KG0NLVDNE' # your Foursquare ID removing it after running
CLIENT_SECRET = 'HKSO0ZTUYTZYWDQCVBSKRX3CD0ITQNEATDQHMSLFMQS4G0FO' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 3RTK0YFFDQHCXD5RAYGWJXMMT1OJ05QBOJVRNU4KG0NLVDNE
CLIENT_SECRET:HKSO0ZTUYTZYWDQCVBSKRX3CD0ITQNEATDQHMSLFMQS4G0FO


In [0]:
LIMIT = 100# limit of number of venues returned by Foursquare API
radius = 500 # define radius

In [0]:
# function to repeat the exploring process to all the neighborhoods in Toronto
import urllib
def getNearbyVenues(names, latitudes, longitudes, radius=500, categoryIds=''):
    try:
        venues_list=[]
        for name, lat, lng in zip(names, latitudes, longitudes):
            #print(name)

            # create the API request URL
            url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, LIMIT)

            if (categoryIds != ''):
                url = url + '&categoryId={}'
                url = url.format(categoryIds)

            # make the GET request
            response = requests.get(url).json()
            results = response["response"]['venues']

            # return only relevant information for each nearby venue
            for v in results:
                success = False
                try:
                    category = v['categories'][0]['name']
                    success = True
                except:
                    pass

                if success:
                    venues_list.append([(
                        name, 
                        lat, 
                        lng, 
                        v['name'], 
                        v['location']['lat'], 
                        v['location']['lng'],
                        v['categories'][0]['name']
                    )])

        nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
        nearby_venues.columns = ['Neighbourhood', 
                  'Latitude', 
                  'Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    except:
        print(url)
        print(response)
        print(results)
        print(nearby_venues)

    return(nearby_venues)

In [145]:
# Use category id 4bf58dd8d48988d16a941735 to get only bakeries in the neighbourhood
bakery_toronto= getNearbyVenues(names=toronto_data['Neighbourhood'], latitudes=toronto_data['Latitude'], longitudes=toronto_data['Longitude'], radius=500, categoryIds='4bf58dd8d48988d16a941735')
bakery_toronto.head()

Neighbourhood  Latitude  ...  Venue Longitude Venue Category
0  Harbourfront,Regent Park  43.65426  ...       -79.362017         Bakery
1  Harbourfront,Regent Park  43.65426  ...       -79.365947  Grocery Store
2  Harbourfront,Regent Park  43.65426  ...       -79.359539         Bakery
3  Harbourfront,Regent Park  43.65426  ...       -79.356651         Bakery
4  Harbourfront,Regent Park  43.65426  ...       -79.365583     Food Truck

[5 rows x 7 columns]

In [146]:
bakery_toronto.shape

(272, 7)

In [0]:
# function to add markers for given venues to map
def addToMap(df, color, existingMap):
    for lat, lng, local, venue, venueCat in zip(df['Venue Latitude'],df['Venue Longitude'],df['Neighbourhood'],df['Venue'],df['Venue Category']):
        label = '{} ({}) - {}'.format(venue, venueCat, local)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7).add_to(existingMap)

In [148]:
map_toronto_bakery = folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(bakery_toronto, 'red', map_toronto_bakery)
map_toronto_bakery

In [149]:
# Use category id 4e67e38e036454776db1fb3a to get only residences in the neighbourhood
toronto_venues_residences = getNearbyVenues(names=toronto_data['Neighbourhood'], latitudes=toronto_data['Latitude'], longitudes=toronto_data['Longitude'], radius=1000, categoryIds='4e67e38e036454776db1fb3a')
toronto_venues_residences.head()

Neighbourhood  ...                            Venue Category
0  Harbourfront,Regent Park  ...  Residential Building (Apartment / Condo)
1  Harbourfront,Regent Park  ...  Residential Building (Apartment / Condo)
2  Harbourfront,Regent Park  ...  Residential Building (Apartment / Condo)
3  Harbourfront,Regent Park  ...  Residential Building (Apartment / Condo)
4  Harbourfront,Regent Park  ...  Residential Building (Apartment / Condo)

[5 rows x 7 columns]

In [150]:
toronto_venues_residences.shape

(1537, 7)

In [151]:
from IPython.display import display
map_toronto_residences= folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(toronto_venues_residences, 'green', map_toronto_residences)
display(map_toronto_residences)

In [152]:
#Use category id 4bf58dd8d48988d13d941735 to get the schools in the neighbourhood
toronto_venues_highschools = getNearbyVenues(names=toronto_data['Neighbourhood'], latitudes=toronto_data['Latitude'], longitudes=toronto_data['Longitude'], radius=1000, categoryIds='4bf58dd8d48988d13d941735')
toronto_venues_highschools.head()

Neighbourhood   Latitude  ...  Venue Longitude Venue Category
0  Harbourfront,Regent Park  43.654260  ...       -79.359429    High School
1   Ryerson,Garden District  43.657162  ...       -79.377955    High School
2   Ryerson,Garden District  43.657162  ...       -79.376154    High School
3   Ryerson,Garden District  43.657162  ...       -79.377681    High School
4   Ryerson,Garden District  43.657162  ...       -79.379778    High School

[5 rows x 7 columns]

In [153]:
toronto_venues_highschools.shape

(188, 7)

In [154]:
map_toronto_highschools= folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(toronto_venues_highschools, 'green', map_toronto_highschools)
map_toronto_highschools

In [0]:
#Using category id 4d4b7105d754a06372d81259 to get college&Universities in the neighborhood

In [156]:
toronto_venues_university = getNearbyVenues(names=toronto_data['Neighbourhood'], latitudes=toronto_data['Latitude'], longitudes=toronto_data['Longitude'], radius=1000, categoryIds='4d4b7105d754a06372d81259')
toronto_venues_university.head()

Neighbourhood  ...                   Venue Category
0  Harbourfront,Regent Park  ...           College Residence Hall
1  Harbourfront,Regent Park  ...                Community College
2  Harbourfront,Regent Park  ...        College Academic Building
3  Harbourfront,Regent Park  ...  College Administrative Building
4  Harbourfront,Regent Park  ...                Community College

[5 rows x 7 columns]

In [157]:
toronto_venues_university.shape

(1185, 7)

In [159]:
map_toronto_university= folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(toronto_venues_university, 'blue', map_toronto_university)
map_toronto_university

In [0]:
# Get all these information into a single dataframe

In [0]:
def addColumn(startDf, columnTitle, dataDf):
    grouped = dataDf.groupby('Neighbourhood').count()
    
    for n in startDf['Neighbourhood']:
        try:
            startDf.loc[startDf['Neighbourhood'] == n,columnTitle] = grouped.loc[n, 'Venue']
        except:
            startDf.loc[startDf['Neighbourhood'] == n,columnTitle] = 0

In [160]:
df_data = toronto_data.copy()
addColumn(df_data, 'Bakery', bakery_toronto)
addColumn(df_data, 'High Schools', toronto_venues_highschools)
addColumn(df_data, 'Residences', toronto_venues_residences)
addColumn(df_data, 'University', toronto_venues_university)

df_data

Postcode           Borough  ... Residences  University
0       M5A  Downtown Toronto  ...       46.0        49.0
1       M5B  Downtown Toronto  ...       50.0        50.0
2       M5C  Downtown Toronto  ...       50.0        50.0
3       M4E      East Toronto  ...       20.0         5.0
4       M5E  Downtown Toronto  ...       49.0        48.0
5       M5G  Downtown Toronto  ...       50.0        50.0
6       M6G  Downtown Toronto  ...       32.0        26.0
7       M5H  Downtown Toronto  ...       50.0        50.0
8       M6H      West Toronto  ...       25.0        18.0
9       M5J  Downtown Toronto  ...       50.0        47.0
10      M6J      West Toronto  ...       48.0        22.0
11      M4K      East Toronto  ...       33.0        19.0
12      M5K  Downtown Toronto  ...       50.0        50.0
13      M6K      West Toronto  ...       49.0        16.0
14      M4L      East Toronto  ...       11.0         5.0
15      M5L  Downtown Toronto  ...       50.0        50.0
16      M4M      East Toronto  ...       24.0         8.0
17      M4N   Central Toronto  ...       12.0        37.0
18      M5N   Central Toronto  ...       25.0        10.0
19      M4P   Central Toronto  ...       49.0        43.0
20      M5P   Central Toronto  ...       44.0        23.0
21      M6P      West Toronto  ...       33.0         9.0
22      M4R   Central Toronto  ...       48.0        26.0
23      M5R   Central Toronto  ...       45.0        50.0
24      M6R      West Toronto  ...       41.0         8.0
25      M4S   Central Toronto  ...       47.0        47.0
26      M5S  Downtown Toronto  ...       48.0        50.0
27      M6S      West Toronto  ...       20.0         3.0
28      M4T   Central Toronto  ...       40.0        17.0
29      M5T  Downtown Toronto  ...       49.0        50.0
30      M4V   Central Toronto  ...       48.0        28.0
31      M5V  Downtown Toronto  ...       47.0         2.0
32      M4W  Downtown Toronto  ...       49.0        20.0
33      M5W  Downtown Toronto  ...       50.0        50.0
34      M4X  Downtown Toronto  ...       46.0        46.0
35      M5X  Downtown Toronto  ...       50.0        50.0
36      M4Y  Downtown Toronto  ...       50.0        50.0
37      M7Y      East Toronto  ...        9.0         3.0

[38 rows x 9 columns]

In [0]:
# negative weight, because my friend wants to open a bakery and thus wants to avoid concurrence as much as possible
weight_bakery = -1

# positive weight, because high school students are good customers
weight_schools = 1

# positive weight because residents of the neighbourhood are the best customers
weight_residences = 3

# positive weight because universities of the neighbourhood are the best customers
weight_university = 2

In [0]:
df_weighted = df_data[['Neighbourhood']].copy()

In [166]:
df_weighted['Score'] = df_data['Bakery'] * weight_bakery + df_data['High Schools'] * weight_schools + df_data['Residences'] * weight_residences + df_data['University'] * weight_university
df_weighted = df_weighted.sort_values(by=['Score'], ascending=False)
df_weighted

Neighbourhood  Score
36                               Church and Wellesley  255.0
26                      Harbord,University of Toronto  251.0
5                                  Central Bay Street  250.0
1                             Ryerson,Garden District  249.0
9     Harbourfront East,Toronto Islands,Union Station  244.0
23                  The Annex,North Midtown,Yorkville  241.0
7                              Adelaide,King,Richmond  240.0
25                                         Davisville  239.0
35              First Canadian Place,Underground city  238.0
19                                   Davisville North  237.0
2                                      St. James Town  237.0
12            Design Exchange,Toronto Dominion Centre  236.0
34                         Cabbagetown,St. James Town  235.0
4                                         Berczy Park  234.0
15                      Commerce Court,Victoria Hotel  234.0
29            Chinatown,Grange Park,Kensington Market  233.0
33                    Stn A PO Boxes 25 The Esplanade  231.0
0                            Harbourfront,Regent Park  229.0
22                                 North Toronto West  206.0
30  Deer Park,Forest Hill SE,Rathnelly,South Hill,...  202.0
32                                           Rosedale  189.0
20                 Forest Hill North,Forest Hill West  183.0
10                            Little Portugal,Trinity  181.0
13         Brockton,Exhibition Place,Parkdale Village  174.0
28                         Moore Park,Summerhill East  154.0
6                                            Christie  147.0
31  CN Tower,Bathurst Quay,Island airport,Harbourf...  146.0
24                              Parkdale,Roncesvalles  136.0
11                        The Danforth West,Riverdale  135.0
21                       High Park,The Junction South  116.0
17                                      Lawrence Park  115.0
8                         Dovercourt Village,Dufferin  109.0
18                                           Roselawn  103.0
16                                    Studio District   85.0
27                                  Runnymede,Swansea   67.0
3                                         The Beaches   66.0
14                      The Beaches West,India Bazaar   41.0
37  Business Reply Mail Processing Centre 969 Eastern   29.0

In [168]:
map_bog_result = folium.Map(location=[latitude, longitude], zoom_start=15)

bog_win = toronto_data[toronto_data['Neighbourhood'] == 'Church and Wellesley']

for lat, lng, local in zip(bog_win['Latitude'], bog_win['Longitude'], bog_win['Neighbourhood']):
    label = '{}'.format(local)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.7).add_to(map_bog_result) 

addToMap(bakery_toronto[bakery_toronto['Neighbourhood'] == 'Church and Wellesley'], 'red', map_bog_result)
addToMap(toronto_venues_highschools[toronto_venues_highschools['Neighbourhood'] == 'Church and Wellesley'], 'green', map_bog_result)
addToMap(toronto_venues_residences[toronto_venues_residences['Neighbourhood'] == 'Church and Wellesley'], 'fuchsia', map_bog_result)
addToMap(toronto_venues_university[toronto_venues_university['Neighbourhood'] == 'Church and Wellesley'], 'yellow', map_bog_result)

map_bog_result

In [0]:
#Church and Wellesley is the best place to open a bakery for my friend 